# Option settings 

In [1]:
n_epochs=10000 #number of epochs of training
batch_size=3000 #size of the batches
lr=0.0001 #adam: learning rate
b1=0.5  #"adam: decay of first order momentum of gradient")
b2=0.999 #adam: decay of first order momentum of gradient")
n_cpu=8
latent_dim=100
img_size=100
channels=3
n_critic=5
clip_value=0.01
sample_interval=1000
img_shape = (channels, img_size, img_size)
crop_size = 400
print(img_shape)

(3, 100, 100)


# Static Code

In [2]:
from tensorboard_logger import configure, log_value
import tensorboard
import argparse
import os
import numpy as np
import math
import sys
import glob
import time
import random
#import utils import Logger

# torchvision stuff
import torchvision.transforms as transforms
from torchvision.utils import save_image
from torchvision import datasets


# torch stuff
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F
import torch.autograd as autograd
import torch
from torch.utils.data import DataLoader
from torch.utils.data import Dataset







from PIL import Image


class ImageDataset(Dataset):
    def __init__(self, folder_path, transforms_=None):
        self.transform = transforms.Compose(transforms_)
        self.files = sorted(glob.glob('%s/*.*' % folder_path))

    def __getitem__(self, index):
        img = Image.open(self.files[index % len(self.files)])
        img = self.transform(img)
        return img

    def __len__(self):
        return len(self.files)
    
    
cuda = True if torch.cuda.is_available() else False
print(cuda)

class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()

        def block(in_feat, out_feat, normalize=True):
            layers = [nn.Linear(in_feat, out_feat)]
            if normalize:
                layers.append(nn.BatchNorm1d(out_feat, 0.8))
            layers.append(nn.LeakyReLU(0.2, inplace=True))
            return layers

        self.model = nn.Sequential(
            *block(100, 128, normalize=False),
            *block(128, 256),
            *block(256, 512),
            *block(512, 1024),
            nn.Linear(1024, int(np.prod(img_shape))),
            nn.Tanh()
        )

    def forward(self, z):
        img = self.model(z)
        img = img.view(img.shape[0], *img_shape)
        return img
    
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()

        self.model = nn.Sequential(
            nn.Linear(int(np.prod(img_shape)), 512),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Linear(512, 256),
            nn.LeakyReLU(0.2, inplace=True),
            nn.Linear(256, 1),
        )

    def forward(self, img):
        img_flat = img.view(img.shape[0], -1)
        validity = self.model(img_flat)
        return validity
    
def compute_gradient_penalty(D, real_samples, fake_samples):
    """Calculates the gradient penalty loss for WGAN GP"""
    # Random weight term for interpolation between real and fake samples
    alpha = Tensor(np.random.random((real_samples.size(0), 1, 1, 1)))
    # Get random interpolation between real and fake samples
    interpolates = (alpha * real_samples + ((1 - alpha) * fake_samples)).requires_grad_(True)
    d_interpolates = D(interpolates)
    fake = Variable(Tensor(real_samples.shape[0], 1).fill_(1.0), requires_grad=False)
    # Get gradient w.r.t. interpolates
    gradients = autograd.grad(
        outputs=d_interpolates,
        inputs=interpolates,
        grad_outputs=fake,
        create_graph=True,
        retain_graph=True,
        only_inputs=True,
    )[0]
    gradients = gradients.view(gradients.size(0), -1)
    gradient_penalty = ((gradients.norm(2, dim=1) - 1) ** 2).mean()
    return gradient_penalty


True


# Initialize Models and Load Settings

In [3]:
# Loss weight for gradient penalty
lambda_gp = 10


# Initialize generator and discriminator
generator = Generator()
discriminator = Discriminator()

# If cuda, use cuda
if cuda:
    generator.cuda()
    discriminator.cuda()
    


In [4]:
lr=0.0001
# Optimizers
optimizer_G = torch.optim.Adam(generator.parameters(), lr=lr, betas=(b1, b2))
optimizer_D = torch.optim.Adam(discriminator.parameters(), lr=lr, betas=(b2, b2))
Tensor = torch.cuda.FloatTensor if cuda else torch.FloatTensor
print(lr)

0.0001


In [5]:
PATH = "/home/jgmeyer2/vangan/gans/models/"
modelname = "zinc250k_rgb100px"
print(PATH+ "G_" + modelname+ ".model")


/home/jgmeyer2/vangan/gans/models/G_zinc250k_rgb100px.model


# Load Previous model

In [6]:

state_g = torch.load(PATH + "G_" + modelname+ ".model")
state_d = torch.load(PATH + "D_" + modelname+ ".model")


generator.load_state_dict(state_g['state_dict'])
optimizer_G.load_state_dict(state_g['optimizer'])

discriminator.load_state_dict(state_d['state_dict'])
optimizer_D.load_state_dict(state_d['optimizer'])




# INitialize logger

In [7]:
configure("runs/color100px_n4",flush_secs=5)

# Training loop

# make training function

In [8]:
def save_models(PATH, modelname):
    os.makedirs(PATH,exist_ok=True)
    ### get generator state, save model
    state_g = {
        'epoch': epoch,
        'state_dict': generator.state_dict(),
        'optimizer': optimizer_G.state_dict()
        }
    torch.save(state_g, PATH+"G_"+modelname+".model")
    ### get discriminator state, save model
    state_d = {
        'epoch': epoch,
        'state_dict': discriminator.state_dict(),
        'optimizer': optimizer_D.state_dict()
        }
    torch.save(state_d, PATH+"D_"+modelname+".model")
    print("model saved")




In [9]:
epoch =0
save_interval = 100
epoch % save_interval


0

In [10]:


def train(dataloader, batch_size, n_epochs, PATH, modelname, save_interval):
    start = time.time()
    batches_done = 0
    for epoch in range(n_epochs):
        batchtimes=[float()]
        if epoch % save_interval == 0:
            save_models(PATH, modelname)
        for i, imgs in enumerate(dataloader):
            ## checkpoint

            # Configure input
            real_imgs = Variable(imgs.type(Tensor))
            # ---------------------
            #  Train Discriminator
            # ---------------------
            optimizer_D.zero_grad()
            # Sample noise as generator input
            z = Variable(Tensor(np.random.normal(0, 1, (imgs.shape[0], latent_dim))))
            # Generate a batch of images
            fake_imgs = generator(z)
            # Real images
            real_validity = discriminator(real_imgs)
            # Fake images
            fake_validity = discriminator(fake_imgs)
            # Gradient penalty
            gradient_penalty = compute_gradient_penalty(discriminator, real_imgs.data, fake_imgs.data)
            # Adversarial loss
            d_loss = -torch.mean(real_validity) + torch.mean(fake_validity) + lambda_gp * gradient_penalty
            d_loss.backward()
            optimizer_D.step()
            optimizer_G.zero_grad()
            # Train the generator every n_critic steps
            if i % n_critic == 0:
                # -----------------
                #  Train Generator
                # -----------------
                # Generate a batch of images
                fake_imgs = generator(z)
                # Loss measures generator's ability to fool the discriminator
                # Train on fake images
                fake_validity = discriminator(fake_imgs)
                g_loss = -torch.mean(fake_validity)
                g_loss.backward()
                optimizer_G.step()
                #logger.log(d_loss, g_loss, epoch, batches_done, num_batches)
                if batches_done % sample_interval ==0:
                    log_value('g_loss', g_loss, batches_done)
                    log_value('d_loss', d_loss, batches_done)

                if batches_done % sample_interval/10 == 0:
                    save_image(fake_imgs.data[:25], "molpics250px_bw/%d_e.png" % batches_done, nrow=5, normalize=True)

                end = time.time()
                batchtime = (end - start)/5

                print(
                    "[Epoch %d/%d] [Batch %d/%d] [D loss: %f] [G loss: %f] [batch time: %f]"
                    % (epoch, n_epochs, i, len(dataloader), d_loss.item(), g_loss.item(), batchtime)
                )
                batchtimes.append(batchtime/batch_size)
                start = time.time()
                batches_done += n_critic
        print("average time per picture = " + str(np.mean(batchtimes)))
        print("minutes per 100,000 pictures = "+ str((np.mean(batchtimes)*100000)/60))

# Input data 

In [11]:
folder_path = "./zinc250k100px/"
n_epochs=10000
#lr=0.00005
batch_size = 2500
transforms_ = [ transforms.ToTensor(),
                transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5)) ]
dataloader = DataLoader(ImageDataset(folder_path, transforms_=transforms_),
                        batch_size=batch_size, shuffle=True, num_workers=6)
train(dataloader, batch_size, n_epochs, PATH, modelname, 100)

model saved
[Epoch 0/10000] [Batch 0/100] [D loss: -4.639227] [G loss: -2.081155] [batch time: 1.545381]
[Epoch 0/10000] [Batch 5/100] [D loss: -4.651740] [G loss: -2.041103] [batch time: 0.291942]
[Epoch 0/10000] [Batch 10/100] [D loss: -4.634622] [G loss: -1.962550] [batch time: 0.312474]
[Epoch 0/10000] [Batch 15/100] [D loss: -4.612073] [G loss: -2.012500] [batch time: 0.306643]
[Epoch 0/10000] [Batch 20/100] [D loss: -4.595688] [G loss: -1.861674] [batch time: 0.295754]
[Epoch 0/10000] [Batch 25/100] [D loss: -4.644108] [G loss: -1.597929] [batch time: 0.300966]
[Epoch 0/10000] [Batch 30/100] [D loss: -4.593132] [G loss: -1.852075] [batch time: 0.300968]
[Epoch 0/10000] [Batch 35/100] [D loss: -4.650813] [G loss: -1.631063] [batch time: 0.302282]
[Epoch 0/10000] [Batch 40/100] [D loss: -4.614583] [G loss: -1.524552] [batch time: 0.301329]
[Epoch 0/10000] [Batch 45/100] [D loss: -4.605496] [G loss: -1.508649] [batch time: 0.304234]
[Epoch 0/10000] [Batch 50/100] [D loss: -4.611458]

[Epoch 4/10000] [Batch 15/100] [D loss: -4.575657] [G loss: -2.534574] [batch time: 0.296770]
[Epoch 4/10000] [Batch 20/100] [D loss: -4.619308] [G loss: -2.495951] [batch time: 0.290918]
[Epoch 4/10000] [Batch 25/100] [D loss: -4.614257] [G loss: -2.459251] [batch time: 0.288585]
[Epoch 4/10000] [Batch 30/100] [D loss: -4.621925] [G loss: -2.657161] [batch time: 0.295025]
[Epoch 4/10000] [Batch 35/100] [D loss: -4.638924] [G loss: -2.025620] [batch time: 0.294578]
[Epoch 4/10000] [Batch 40/100] [D loss: -4.657590] [G loss: -2.624135] [batch time: 0.299579]
[Epoch 4/10000] [Batch 45/100] [D loss: -4.575763] [G loss: -2.926316] [batch time: 0.294067]
[Epoch 4/10000] [Batch 50/100] [D loss: -4.595305] [G loss: -2.173596] [batch time: 0.292412]
[Epoch 4/10000] [Batch 55/100] [D loss: -4.593608] [G loss: -2.228531] [batch time: 0.293523]
[Epoch 4/10000] [Batch 60/100] [D loss: -4.548036] [G loss: -2.662261] [batch time: 0.293073]
[Epoch 4/10000] [Batch 65/100] [D loss: -4.578302] [G loss: 

[Epoch 8/10000] [Batch 30/100] [D loss: -4.641643] [G loss: -2.690762] [batch time: 0.290489]
[Epoch 8/10000] [Batch 35/100] [D loss: -4.604353] [G loss: -2.901478] [batch time: 0.291863]
[Epoch 8/10000] [Batch 40/100] [D loss: -4.589087] [G loss: -2.758702] [batch time: 0.297656]
[Epoch 8/10000] [Batch 45/100] [D loss: -4.534008] [G loss: -2.615189] [batch time: 0.296239]
[Epoch 8/10000] [Batch 50/100] [D loss: -4.633576] [G loss: -2.458039] [batch time: 0.292443]
[Epoch 8/10000] [Batch 55/100] [D loss: -4.659712] [G loss: -2.719332] [batch time: 0.292174]
[Epoch 8/10000] [Batch 60/100] [D loss: -4.597210] [G loss: -2.370048] [batch time: 0.293868]
[Epoch 8/10000] [Batch 65/100] [D loss: -4.589379] [G loss: -1.989936] [batch time: 0.292443]
[Epoch 8/10000] [Batch 70/100] [D loss: -4.560721] [G loss: -2.525674] [batch time: 0.293686]
[Epoch 8/10000] [Batch 75/100] [D loss: -4.638845] [G loss: -2.427369] [batch time: 0.292251]
[Epoch 8/10000] [Batch 80/100] [D loss: -4.617429] [G loss: 

[Epoch 12/10000] [Batch 45/100] [D loss: -4.655359] [G loss: -1.858078] [batch time: 0.286797]
[Epoch 12/10000] [Batch 50/100] [D loss: -4.678815] [G loss: -1.717871] [batch time: 0.288893]
[Epoch 12/10000] [Batch 55/100] [D loss: -4.660763] [G loss: -2.036595] [batch time: 0.288239]
[Epoch 12/10000] [Batch 60/100] [D loss: -4.617204] [G loss: -1.640110] [batch time: 0.287530]
[Epoch 12/10000] [Batch 65/100] [D loss: -4.662066] [G loss: -1.915903] [batch time: 0.285409]
[Epoch 12/10000] [Batch 70/100] [D loss: -4.607387] [G loss: -1.750033] [batch time: 0.285980]
[Epoch 12/10000] [Batch 75/100] [D loss: -4.637067] [G loss: -2.330250] [batch time: 0.286143]
[Epoch 12/10000] [Batch 80/100] [D loss: -4.633811] [G loss: -1.942451] [batch time: 0.288437]
[Epoch 12/10000] [Batch 85/100] [D loss: -4.631535] [G loss: -1.875074] [batch time: 0.287611]
[Epoch 12/10000] [Batch 90/100] [D loss: -4.623234] [G loss: -1.786342] [batch time: 0.284510]
[Epoch 12/10000] [Batch 95/100] [D loss: -4.622324

[Epoch 16/10000] [Batch 60/100] [D loss: -4.727821] [G loss: -1.392084] [batch time: 0.286528]
[Epoch 16/10000] [Batch 65/100] [D loss: -4.712633] [G loss: -0.789104] [batch time: 0.286912]
[Epoch 16/10000] [Batch 70/100] [D loss: -4.678611] [G loss: -1.521578] [batch time: 0.287483]
[Epoch 16/10000] [Batch 75/100] [D loss: -4.649989] [G loss: -1.229871] [batch time: 0.288687]
[Epoch 16/10000] [Batch 80/100] [D loss: -4.727700] [G loss: -1.994246] [batch time: 0.284937]
[Epoch 16/10000] [Batch 85/100] [D loss: -4.680388] [G loss: -1.163355] [batch time: 0.287367]
[Epoch 16/10000] [Batch 90/100] [D loss: -4.664560] [G loss: -1.883391] [batch time: 0.282834]
[Epoch 16/10000] [Batch 95/100] [D loss: -4.634130] [G loss: -1.353142] [batch time: 0.279136]
average time per picture = 0.00011383904139200848
minutes per 100,000 pictures = 0.18973173565334747
[Epoch 17/10000] [Batch 0/100] [D loss: -4.689421] [G loss: -1.079897] [batch time: 0.500815]
[Epoch 17/10000] [Batch 5/100] [D loss: -4.64

...

[Epoch 2574/10000] [Batch 95/100] [D loss: -5.137935] [G loss: -8.150446] [batch time: 0.285204]
average time per picture = 0.00011837504523141043
minutes per 100,000 pictures = 0.1972917420523507
[Epoch 2575/10000] [Batch 0/100] [D loss: -5.157139] [G loss: -8.707775] [batch time: 0.507030]
[Epoch 2575/10000] [Batch 5/100] [D loss: -5.257246] [G loss: -7.633103] [batch time: 0.325077]
[Epoch 2575/10000] [Batch 10/100] [D loss: -5.240122] [G loss: -8.417988] [batch time: 0.310417]
[Epoch 2575/10000] [Batch 15/100] [D loss: -5.202022] [G loss: -7.926548] [batch time: 0.311521]
[Epoch 2575/10000] [Batch 20/100] [D loss: -5.223434] [G loss: -7.501607] [batch time: 0.302419]
[Epoch 2575/10000] [Batch 25/100] [D loss: -5.177170] [G loss: -8.209349] [batch time: 0.300135]
[Epoch 2575/10000] [Batch 30/100] [D loss: -5.139431] [G loss: -7.675450] [batch time: 0.292348]
[Epoch 2575/10000] [Batch 35/100] [D loss: -5.180352] [G loss: -8.262117] [batch time: 0.295950]
[Epoch 2575/10000] [Batch 40/

average time per picture = 0.00012040016628447032
minutes per 100,000 pictures = 0.20066694380745054
[Epoch 2579/10000] [Batch 0/100] [D loss: -5.201672] [G loss: -7.584614] [batch time: 0.528224]
[Epoch 2579/10000] [Batch 5/100] [D loss: -5.242321] [G loss: -8.117381] [batch time: 0.322342]
[Epoch 2579/10000] [Batch 10/100] [D loss: -5.156849] [G loss: -7.619225] [batch time: 0.309181]
[Epoch 2579/10000] [Batch 15/100] [D loss: -5.196513] [G loss: -8.233440] [batch time: 0.303471]
[Epoch 2579/10000] [Batch 20/100] [D loss: -5.185216] [G loss: -7.912756] [batch time: 0.294952]
[Epoch 2579/10000] [Batch 25/100] [D loss: -5.175893] [G loss: -7.771963] [batch time: 0.297288]
[Epoch 2579/10000] [Batch 30/100] [D loss: -5.189902] [G loss: -7.733948] [batch time: 0.291517]
[Epoch 2579/10000] [Batch 35/100] [D loss: -5.196187] [G loss: -7.875625] [batch time: 0.295566]
[Epoch 2579/10000] [Batch 40/100] [D loss: -5.159232] [G loss: -8.757039] [batch time: 0.308152]
[Epoch 2579/10000] [Batch 45

[Epoch 2583/10000] [Batch 0/100] [D loss: -5.133095] [G loss: -8.240592] [batch time: 0.529334]
[Epoch 2583/10000] [Batch 5/100] [D loss: -5.121017] [G loss: -8.970256] [batch time: 0.345093]
[Epoch 2583/10000] [Batch 10/100] [D loss: -5.152415] [G loss: -8.176454] [batch time: 0.309511]
[Epoch 2583/10000] [Batch 15/100] [D loss: -5.161050] [G loss: -7.821292] [batch time: 0.303271]
[Epoch 2583/10000] [Batch 20/100] [D loss: -5.208289] [G loss: -8.606295] [batch time: 0.297113]
[Epoch 2583/10000] [Batch 25/100] [D loss: -5.138038] [G loss: -8.596256] [batch time: 0.299483]
[Epoch 2583/10000] [Batch 30/100] [D loss: -5.150159] [G loss: -8.196728] [batch time: 0.298396]
[Epoch 2583/10000] [Batch 35/100] [D loss: -5.201052] [G loss: -8.274742] [batch time: 0.297114]
[Epoch 2583/10000] [Batch 40/100] [D loss: -5.075342] [G loss: -8.059834] [batch time: 0.302120]
[Epoch 2583/10000] [Batch 45/100] [D loss: -5.067223] [G loss: -8.896007] [batch time: 0.296594]
[Epoch 2583/10000] [Batch 50/100

Process Process-15510:
Process Process-15505:
Process Process-15509:
Process Process-15506:
Process Process-15508:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/jgmeyer2/anaconda3/envs/vangan/lib/pyt

KeyboardInterrupt: 

# Save models

In [ ]:
def save_models(PATH, modelname, interval, epoch):
    os.makedirs(PATH,exist_ok=True)
    PATH = "/home/jgmeyer2/vangan/gans/models/"
    modelid="250px_jpegs_bw_lr0p00005_2469ep"
epoch=100

state_g = {
    'epoch': epoch,
    'state_dict': generator.state_dict(),
    'optimizer': optimizer_G.state_dict()
    }
torch.save(state_g, PATH+"g"+modelid+".model")

state_d = {
    'epoch': epoch,
    'state_dict': discriminator.state_dict(),
    'optimizer': optimizer_D.state_dict()
    }
torch.save(state_d, PATH+"d"+modelid+".model")
print("saved models @")
print(epoch)




# view training process

In [12]:
#tensorboard
!python -m tensorboard.main --logdir runs

TensorBoard 1.10.0 at http://minilearn:6006 (Press CTRL+C to quit)
W0921 08:28:39.739150 Thread-1 application.py:276] path /[[_dataImageSrc]] not found, sending 404
W0921 08:28:39.739150 140029020059392 application.py:276] path /[[_dataImageSrc]] not found, sending 404
W0921 08:28:39.741382 Thread-2 application.py:276] path /[[_imageURL]] not found, sending 404
W0921 08:28:39.741382 140029011666688 application.py:276] path /[[_imageURL]] not found, sending 404
W0921 08:29:24.286064 Thread-5 application.py:276] path /[[_dataImageSrc]] not found, sending 404
W0921 08:29:24.286064 140028978095872 application.py:276] path /[[_dataImageSrc]] not found, sending 404
W0921 08:29:24.306011 Thread-5 application.py:276] path /[[_imageURL]] not found, sending 404
W0921 08:29:24.306011 140028978095872 application.py:276] path /[[_imageURL]] not found, sending 404
^C
